In [1]:
import yfinance as yf
import numpy as np
import pandas as pd
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor
from sklearn.svm import SVR
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense, Dropout
import matplotlib.pyplot as plt
from datetime import datetime, timedelta

# Define utility functions
def compute_rsi(data, window):
    # Compute Relative Strength Index
    pass  # Placeholder - Replace with the actual function body

def compute_bollinger_bands(data, window):
    # Compute Bollinger Bands
    pass  # Placeholder - Replace with the actual function body

def create_dataset(dataset, look_back=1):
    # Create dataset for LSTM model
    pass  # Placeholder - Replace with the actual function body

def get_data(ticker_symbol, start_date, end_date):
    ticker_data = yf.Ticker(ticker_symbol)
    historical_data = ticker_data.history(start=start_date, end=end_date)
    return historical_data[['Close', 'Volume']].copy()

def mean_absolute_percentage_error(y_true, y_pred, epsilon=1e-10):
    return np.mean(np.abs((y_true - y_pred) / (y_true + epsilon))) * 100

def predict_future(model, initial_input, steps, is_lstm=False):
    future_predictions = []
    current_input = initial_input.copy()
    
    for i in range(steps):
        if is_lstm:
            current_prediction = model.predict(current_input[np.newaxis, :, :])[0, 0]
            future_predictions.append(current_prediction)
            current_input = np.roll(current_input, -1, axis=0)
            current_input[-1, 0] = current_prediction
        else:
            current_prediction = model.predict(current_input[-1, :].reshape(1, -1))
            future_predictions.append(current_prediction[0])
            current_input = np.roll(current_input, -1, axis=0)
            current_input[-1, 0] = current_prediction[0]
    
    return future_predictions

# Main script starts here
ticker_symbol = 'SPY'
start_date = '2023-01-01'
end_date = '2023-10-01'

# Get historical data
data = get_data(ticker_symbol, start_date, end_date)

# Compute technical indicators
data['RSI'] = compute_rsi(data['Close'], 14)  # Example RSI window
data['SMA'] = data['Close'].rolling(window=14).mean()  # Example SMA window
upper_band, lower_band = compute_bollinger_bands(data, 20)  # Example Bollinger Bands window
data['Upper_Band'] = upper_band
data['Lower_Band'] = lower_band

data.dropna(inplace=True)

# Normalize data
scaler = MinMaxScaler(feature_range=(0, 1))
data_scaled = scaler.fit_transform(data)

# Create dataset for training
look_back = 10  # This is an example value
X, y = create_dataset(data_scaled, look_back)

# Split into training and test sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=24)

# Define and train multiple models
models = {
    "Linear Regression": LinearRegression(),
    "Random Forest": RandomForestRegressor(n_estimators=200, random_state=24),
    "Gradient Boosting": GradientBoostingRegressor(n_estimators=200, random_state=24),
    "SVR": SVR(kernel='rbf', C=1e3, gamma=0.1),
    "LSTM": Sequential([
        LSTM(100, input_shape=(X_train.shape[1], X_train.shape[2]), return_sequences=True),
        Dropout(0.2),
        LSTM(50, return_sequences=True),
        Dropout(0.2),
        LSTM(25),
        Dense(1)
    ])
}

models["LSTM"].compile(optimizer='adam', loss='mean_squared_error')

# Train the models
for model_name, model in models.items():
    if model_name == "LSTM":
        model.fit(X_train, y_train, epochs=5, batch_size=1, verbose=1)
    else:
        model.fit(X_train, y_train)

# Evaluate the models
test_results = {}
for model_name, model in models.items():
    predictions = model.predict(X_test)
    if model_name == "LSTM":
        predictions = predictions[:, 0]  # Flatten LSTM predictions
    mape = mean_absolute_percentage_error(y_test, predictions)
    test_results[model_name] = mape
    print(f"{model_name} MAPE: {mape}")

# Prediction and plotting function
def plot_predictions(real_data, predictions, dates):
    plt.figure(figsize=(10, 6))
    plt.plot(dates, real_data, label='Real Prices', color='black')
    plt.plot(dates, predictions, label='Predicted Prices', color='cyan', linestyle='--')
    plt.title('Stock Price Predictions')
    plt.xlabel('Date')
    plt.ylabel('Price')
    plt.legend()
    plt.show()

# Make predictions with the best model
best_model_name = min(test_results, key=test_results.get)
best_model = models[best_model_name]

# Prepare data for prediction
last_10_days_scaled = data_scaled[-look_back:]
dates = pd.to_datetime(data.index[-10:])

# Make predictions
if best_model_name == "LSTM":
    predictions = predict_future(best_model, last_10_days_scaled, 10, is_lstm=True)
else:
    predictions = predict_future(best_model, last_10_days_scaled, 10, is_lstm=False)

# Rescale predictions back to original range
predictions_rescaled = scaler.inverse_transform(np.hstack([
    np.array(predictions).reshape(-1, 1),
    np.zeros((len(predictions), data_scaled.shape[1]-1))
]))[:, 0]

# Plot the predictions
plot_predictions(data['Close'][-10:], predictions_rescaled, dates)

# If you need to save the models, you can use joblib or the save method for Keras models
# Example: joblib.dump(models['Random Forest'], 'random_forest_model.joblib')
# Example: models['LSTM'].save('lstm_model.h5')


TypeError: cannot unpack non-iterable NoneType object

In [2]:
import yfinance as yf
import numpy as np
import pandas as pd
from sklearn.preprocessing import MinMaxScaler
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor
from sklearn.model_selection import train_test_split
from sklearn.svm import SVR
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense, Dropout
import matplotlib.pyplot as plt
from datetime import datetime, timedelta

# Define functions used in the script

def compute_rsi(data, window):
    delta = data.diff()
    up, down = delta.copy(), delta.copy()
    up[up < 0] = 0
    down[down > 0] = 0
    
    roll_up = up.rolling(window=window).mean()
    roll_down = down.abs().rolling(window=window).mean()
    
    RS = roll_up / roll_down
    RSI = 100.0 - (100.0 / (1.0 + RS))
    
    return RSI

def compute_bollinger_bands(data, window):
    sma = data['Close'].rolling(window=window).mean()
    rolling_std = data['Close'].rolling(window=window).std()
    upper_band = sma + (rolling_std * 2)
    lower_band = sma - (rolling_std * 2)
    
    return upper_band, lower_band

def create_dataset(dataset, look_back=1):
    dataX, dataY = [], []
    for i in range(len(dataset)-look_back-1):
        a = dataset[i:(i+look_back), 0]
        dataX.append(a)
        dataY.append(dataset[i + look_back, 0])
    return np.array(dataX), np.array(dataY)

# Main function to execute your workflow
def main():
    # Initialize the ticker
    ticker_symbol = 'SPY'
    ticker_data = yf.Ticker(ticker_symbol)

    # Define start and end dates for fetching historical data
    start_date = '2023-01-01'
    end_date = '2023-10-01'
    historical_data = ticker_data.history(start=start_date, end=end_date)

    # Preprocess data and compute features
    data = historical_data[['Close', 'Volume']].copy()
    data['RSI'] = compute_rsi(data['Close'], 14)  # Example RSI window
    data['SMA'] = data['Close'].rolling(window=14).mean()  # Example SMA window
    upper_band, lower_band = compute_bollinger_bands(data, 20)  # Example Bollinger Bands window
    data['Upper_Band'] = upper_band
    data['Lower_Band'] = lower_band
    data.dropna(inplace=True)

    # Data scaling
    scaler = MinMaxScaler(feature_range=(0, 1))
    data_scaled = scaler.fit_transform(data[['Close', 'Volume', 'RSI', 'SMA', 'Upper_Band', 'Lower_Band']])
    look_back = 10
    X, y = create_dataset(data_scaled, look_back)
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=0)

    # Model initialization and training
    model = Sequential([
        LSTM(50, return_sequences=True, input_shape=(look_back, data_scaled.shape[1])),
        Dropout(0.2),
        LSTM(50, return_sequences=False),
        Dropout(0.2),
        Dense(1)
    ])
    model.compile(optimizer='adam', loss='mean_squared_error')
    model.fit(X_train, y_train, epochs=5, batch_size=1, verbose=1)
    # Predict future prices
    predictions = []
    current_batch = X[-1:]  # Get the last batch of data
    for i in range(10):  # Predict the next 10 days
        current_pred = model.predict(current_batch)[0]
        predictions.append(current_pred)
        current_batch = np.append(current_batch[:, 1:, :], [[current_pred]], axis=1)
    predictions = scaler.inverse_transform(np.array(predictions).reshape(-1, 1))

    # Plot the results
    plt.figure(figsize=(12, 6))
    plt.plot(data.index[-10:], data['Close'][-10:], label='Actual Closing Prices')
    future_dates = pd.date_range(start=data.index[-1], periods=11, closed='right')
    plt.plot(future_dates, predictions, label='Predicted Closing Prices')
    plt.title('Stock Price Prediction')
    plt.xlabel('Date')
    plt.ylabel('Price')
    plt.legend()
    plt.show()

# Run the main function
if __name__ == "__main__":
    main()


Epoch 1/5


ValueError: in user code:

    File "B:\AC\lib\site-packages\keras\src\engine\training.py", line 1377, in train_function  *
        return step_function(self, iterator)
    File "B:\AC\lib\site-packages\keras\src\engine\training.py", line 1360, in step_function  **
        outputs = model.distribute_strategy.run(run_step, args=(data,))
    File "B:\AC\lib\site-packages\keras\src\engine\training.py", line 1349, in run_step  **
        outputs = model.train_step(data)
    File "B:\AC\lib\site-packages\keras\src\engine\training.py", line 1126, in train_step
        y_pred = self(x, training=True)
    File "B:\AC\lib\site-packages\keras\src\utils\traceback_utils.py", line 70, in error_handler
        raise e.with_traceback(filtered_tb) from None
    File "B:\AC\lib\site-packages\keras\src\engine\input_spec.py", line 235, in assert_input_compatibility
        raise ValueError(

    ValueError: Exception encountered when calling layer 'sequential' (type Sequential).
    
    Input 0 of layer

In [13]:
import yfinance as yf
import numpy as np
import pandas as pd
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import train_test_split
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense, Dropout

# Utility functions
def compute_rsi(data, window):
    delta = data.diff()
    up, down = delta.copy(), delta.copy()
    up[up < 0] = 0
    down[down > 0] = 0
    
    roll_up = up.rolling(window=window).mean()
    roll_down = down.abs().rolling(window=window).mean()
    
    RS = roll_up / roll_down
    RSI = 100.0 - (100.0 / (1.0 + RS))
    
    return RSI

def compute_bollinger_bands(data, window):
    sma = data['Close'].rolling(window=window).mean()
    rolling_std = data['Close'].rolling(window=window).std()
    upper_band = sma + (rolling_std * 2)
    lower_band = sma - (rolling_std * 2)
    
    return upper_band, lower_band

def create_dataset(dataset, look_back=1):
    dataX, dataY = [], []
    for i in range(len(dataset) - look_back - 1):
        a = dataset[i:(i + look_back), :]
        dataX.append(a)
        dataY.append(dataset[i + look_back, 0])
    return np.array(dataX), np.array(dataY)

# Get and process data
ticker_symbol = 'SPY'
start_date = '2023-01-01'
end_date = '2023-10-01'
data = yf.download(ticker_symbol, start=start_date, end=end_date)
data['RSI'] = compute_rsi(data['Close'], 14)
data['SMA'] = data['Close'].rolling(window=14).mean()
upper_band, lower_band = compute_bollinger_bands(data, 20)
data['Upper_Band'] = upper_band
data['Lower_Band'] = lower_band

data.dropna(inplace=True)
data_scaled = MinMaxScaler(feature_range=(0, 1)).fit_transform(data[['Close', 'Volume', 'RSI', 'SMA', 'Upper_Band', 'Lower_Band']])

# Create dataset for LSTM
look_back = 10
X, y = create_dataset(data_scaled, look_back)
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=24)

# Reshape X for LSTM [samples, time steps, features]
X_train = np.reshape(X_train, (X_train.shape[0], look_back, data_scaled.shape[1]))
X_test = np.reshape(X_test, (X_test.shape[0], look_back, data_scaled.shape[1]))

# Build and compile LSTM model
model = Sequential([
    LSTM(50, return_sequences=True, input_shape=(look_back, data_scaled.shape[1])),
    Dropout(0.2),
    LSTM(50, return_sequences=False),
    Dropout(0.2),
    Dense(1)
])
model.compile(optimizer='adam', loss='mean_squared_error')

# Train the model
model.fit(X_train, y_train, epochs=50, batch_size=32, validation_data=(X_test, y_test), verbose=1)
def predict_future(model, data_scaled, look_back, num_predictions):
    predictions = []
    current_batch = data_scaled[-look_back:]  # Last `look_back` days
    current_batch = current_batch.reshape(1, look_back, data_scaled.shape[1])

    for _ in range(num_predictions):
        # Predicting the next step and obtaining the predicted value
        current_pred = model.predict(current_batch)[0]
        # Reshaping the prediction to match the batch dimensionality
        current_pred = current_pred.reshape(1, 1, data_scaled.shape[1])
        # Append the prediction to the current batch for the next prediction
        current_batch = np.append(current_batch[:, 1:, :], current_pred, axis=1)
        # Appending the predicted value to the predictions list
        predictions.append(current_pred.flatten())

    # Flatten the predictions to remove unnecessary dimensions
    return np.array(predictions).reshape(num_predictions, data_scaled.shape[1])

# Your code for making predictions and inverse transforming the results follows here

# Make predictions
num_predictions = 10
future_predictions_scaled = predict_future(model, data_scaled, look_back, num_predictions)

# Inverse transform the predictions to get actual price predictions
future_prices = MinMaxScaler(feature_range=(0, 1)).fit(data[['Close']]).inverse_transform(future_predictions_scaled)

# Get real future prices for comparison (if available)
# If the future dates are not available yet, this will return an empty DataFrame
future_dates = pd.bdate_range(start=data.index[-1] + pd.Timedelta(days=1), periods=num_predictions, freq='B')
real_future_data = yf.download(ticker_symbol, start=future_dates[0], end=future_dates[-1])
real_future_prices = real_future_data['Close'].values if not real_future_data.empty else []

# Visualize the results
import matplotlib.pyplot as plt

plt.figure(figsize=(14, 7))
plt.plot(data.index[-num_predictions:], data['Close'][-num_predictions:], color='blue', label='Historical Prices')
plt.plot(future_dates, future_prices, color='red', label='Predicted Prices')
if len(real_future_prices) > 0:
    plt.plot(future_dates[:len(real_future_prices)], real_future_prices, color='green', label='Real Future Prices')
plt.title(f'{ticker_symbol} Price Prediction')
plt.xlabel('Date')
plt.ylabel('Price')
plt.legend()
plt.show()


[*********************100%***********************]  1 of 1 completed
Epoch 1/50
4/4 [==============================] - 3s 195ms/step - loss: 0.1282 - val_loss: 0.0130
Epoch 2/50
4/4 [==============================] - 0s 15ms/step - loss: 0.0358 - val_loss: 0.0460
Epoch 3/50
4/4 [==============================] - 0s 14ms/step - loss: 0.0310 - val_loss: 0.0113
Epoch 4/50
4/4 [==============================] - 0s 14ms/step - loss: 0.0173 - val_loss: 0.0209
Epoch 5/50
4/4 [==============================] - 0s 14ms/step - loss: 0.0286 - val_loss: 0.0175
Epoch 6/50
4/4 [==============================] - 0s 13ms/step - loss: 0.0188 - val_loss: 0.0097
Epoch 7/50
4/4 [==============================] - 0s 14ms/step - loss: 0.0159 - val_loss: 0.0129
Epoch 8/50
4/4 [==============================] - 0s 14ms/step - loss: 0.0160 - val_loss: 0.0114
Epoch 9/50
4/4 [==============================] - 0s 13ms/step - loss: 0.0137 - val_loss: 0.0088
Epoch 10/50
4/4 [==============================] - 0s 15m

ValueError: cannot reshape array of size 1 into shape (1,1,6)